# RWKV v5-headsize2x / embedding init-range 1e-01 / 4k

- 6 layers
- 2048 embedding size

Going through the modified memory training for v5 models, across various initial embedding model weights

**Note:** This project assumes you have the rwkv-infctx conda env setup

# Basic Setup

In [1]:
# First lets setup the various directories, and init the model
!mkdir -p ../../../../model/
!mkdir -p ../../../../datapath/
!mkdir -p ../../../../checkpoint/

In [2]:
# Additional dependencies for eval stuff
!pip install -q aiocsv aiofiles


[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python3.11 -m pip install --upgrade pip


In [3]:
DEEPSPEED_STRAT="deepspeed_stage_1"
GPU_DEVICES="auto"
ENABLE_WANDB=True

RWKV_WAVENET_LAYERS=1

EMBED_SCALE=0.1
EMBED_SCALE_LABEL=str(EMBED_SCALE).replace(".", "_")

LAYER_COUNT=6
EMBED_DIM=2048

WANDB_PREFIX=f"v5-hs32-L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE}"
FILENAME_PREFIX=f"v5-hs32-L{LAYER_COUNT}-D{EMBED_DIM}-E{EMBED_SCALE_LABEL}"

print("DEEPSPEED_STRAT:", DEEPSPEED_STRAT)
print("ENABLE_WANDB:", ENABLE_WANDB)
print("GPU_DEVICES:", GPU_DEVICES)

if ENABLE_WANDB:
    WANDB_MODE="online"
else:
    WANDB_MODE="disabled"

# Computing the notebook, and various paths
import os
NOTEBOOK_DIR=os.path.dirname(os.path.abspath("__file__"))
PROJECT_DIR=os.path.abspath(os.path.join(NOTEBOOK_DIR, "../../../../"))
TRAINER_DIR=os.path.abspath(os.path.join(PROJECT_DIR, "./RWKV-v5headsize32/"))
INFERENCE_DIR=os.path.abspath(os.path.join(PROJECT_DIR, "./RWKV-v5headsize32/"))

print("NOTEBOOK_DIR:", NOTEBOOK_DIR)
print("INFERENCE_DIR:", INFERENCE_DIR)
print("TRAINER_DIR:", TRAINER_DIR)
print("PROJECT_DIR:", PROJECT_DIR)

DEEPSPEED_STRAT: deepspeed_stage_1
ENABLE_WANDB: True
GPU_DEVICES: auto
NOTEBOOK_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32
INFERENCE_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize32
TRAINER_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/RWKV-v5headsize32
PROJECT_DIR: /actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer


In [4]:
# Init the model
!cd "{TRAINER_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python3 ./init_model.py \
        --n_layer "{LAYER_COUNT}" --n_embd "{EMBED_DIM}" \
        --emb-scale "{EMBED_SCALE}" \
        --vocab_size neox --skip-if-exists \
        "../model/{FILENAME_PREFIX}-neox-init.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'
---- Initializing model ----
No of layers: 6
Embedding size: 2048
Output model path: ../model/v5-hs32-L6-D2048-E0_1-neox-init.pth
Vocab size: 50277
Emb scale: 0.1
Note: this process takes a significant time (and ram) for large models
---- ----- ----


50277 2048  -0.1 emb.weight


2048  2048  1.0  blocks.0.att.receptance.weight


2048  2048  1.0  blocks.0.att.key.weight


...

2048  2048  0    blocks.4.ffn.receptance.weight
2048  8192  0    blocks.4.ffn.value.weight
2048  2048  1.0  blocks.5.att.receptance.weight


2048  2048  1.0  blocks.5.att.key.weight


2048  2048  1.0  blocks.5.att.value.weight


2048  2048  0    blocks.5.att.output.weight
8192  2048  1.0  blocks.5.ffn.key.weight


2048  2048  0    blocks.5.ffn.receptance.weight
2048  8192  0    blocks.5.ffn.value.weight
50277 2048  0.5  head.weight


## Enwiki Stage 1 : Foundation 4k model training

In [5]:
# Lets preload the requried dataset 
!cd "{TRAINER_DIR}" && \
    python3 preload_datapath.py "{NOTEBOOK_DIR}/v5base-enwiki-4k.yaml"

Found cached dataset parquet (/actions-runner/.cache/huggingface/datasets/teven___parquet/teven--enwiki_100k-1359e81b212c2dd6/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7)
100%|█████████████████████████████████████████████| 1/1 [00:00<00:00, 62.17it/s]


Loading cached processed dataset at /actions-runner/.cache/huggingface/datasets/teven___parquet/teven--enwiki_100k-1359e81b212c2dd6/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-ddfe836637577ca9_*_of_00064.arrow


Loading cached processed dataset at /actions-runner/.cache/huggingface/datasets/teven___parquet/teven--enwiki_100k-1359e81b212c2dd6/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-4d4a43715cf9c5ec_*_of_00064.arrow


Loading cached processed dataset at /actions-runner/.cache/huggingface/datasets/teven___parquet/teven--enwiki_100k-1359e81b212c2dd6/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-e272537be34aded3_*_of_00064.arrow
Loading cached split indices for dataset at /actions-runner/.cache/huggingface/datasets/teven___parquet/teven--enwiki_100k-1359e81b212c2dd6/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-52422a63e6f04b92.arrow and /actions-runner/.cache/huggingface/datasets/teven___parquet/teven--enwiki_100k-1359e81b212c2dd6/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-2eab36f5d1f93a5f.arrow


Saving the dataset (0/5 shards):   0%|         | 0/81487 [00:00<?, ? examples/s]

...

Saving the dataset (3/5 shards):  75%|▋| 60893/81487 [00:02<00:00, 30172.21 exam

Saving the dataset (4/5 shards):  80%|▊| 65190/81487 [00:02<00:00, 30366.09 exam

Saving the dataset (4/5 shards):  85%|▊| 69190/81487 [00:02<00:00, 30046.04 exam

Saving the dataset (4/5 shards):  90%|▉| 73190/81487 [00:02<00:00, 30289.86 exam

Saving the dataset (4/5 shards):  95%|▉| 77190/81487 [00:02<00:00, 30436.21 exam

In [6]:
# Start the foundation model training
!cd "{TRAINER_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    export WANDB_MODE="{WANDB_MODE}" && \
    python lightning_trainer.py fit \
        -c "{NOTEBOOK_DIR}/v5base-enwiki-4k.yaml" \
        --trainer.logger.init_args.name="{WANDB_PREFIX} - Enwiki-4k Foundation (train-ctx=4k, {DEEPSPEED_STRAT})" \
        --trainer.strategy="{DEEPSPEED_STRAT}" \
        --trainer.devices="{GPU_DEVICES}" \
        --trainer.callbacks.init_args.dirpath="../checkpoint/{FILENAME_PREFIX}-enwiki-4k/" \
        --model.load_model="../model/{FILENAME_PREFIX}-neox-init.pth" \
        --model.ctx_len=4096 \
        --model.bptt_learning_range=1

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


/usr/local/lib/python3.11/dist-packages/lightning/pytorch/cli.py:484: UserWarning: LightningCLI's args parameter is intended to run from within Python like if it were from the command line. To prevent mistakes it is not recommended to provide both args and command line arguments, got: sys.argv[1:]=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32/v5base-enwiki-4k.yaml', '--trainer.logger.init_args.name=v5-hs32-L6-D2048-E0.1 - Enwiki-4k Foundation (train-ctx=4k, deepspeed_stage_1)', '--trainer.strategy=deepspeed_stage_1', '--trainer.devices=auto', '--trainer.callbacks.init_args.dirpath=../checkpoint/v5-hs32-L6-D2048-E0_1-enwiki-4k/', '--model.load_model=../model/v5-hs32-L6-D2048-E0_1-neox-init.pth', '--model.ctx_len=4096', '--model.bptt_learning_range=1'], args=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32/v5base-enwiki-4k.yaml', '--trainer.

/usr/local/lib/python3.11/dist-packages/lightning/fabric/utilities/seed.py:39: UserWarning: No seed found, seed set to 2002234927
  rank_zero_warn(f"No seed found, seed set to {seed}")
Global seed set to 2002234927


wandb: Currently logged in as: picocreator (rwkv-x-dev). Use `wandb login --relogin` to force relogin


...


Validation DataLoader 0: 100%|██████████████████| 52/52 [00:16<00:00,  3.14it/s]

Epoch 0: 100%|█| 10186/10186 [2:47:01<00:00,  1.02it/s, v_num=0gjq, train/loss=3
Epoch 0: 100%|█| 10186/10186 [2:47:01<00:00,  1.02it/s, v_num=0gjq, train/loss=3

`Trainer.fit` stopped: `max_epochs=1` reached.
Epoch 0: 100%|█| 10186/10186 [2:47:07<00:00,  1.02it/s, v_num=0gjq, train/loss=3


wandb: Waiting for W&B process to finish... (success).


wandb: 
wandb: Run history:
wandb:              batchidx ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb:                 epoch ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:           global_rank ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:          real_ctx_len ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:               substep ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb:            train/loss █▇▆▅▅▅▄▄▄▄▄▄▃▄▃▃▂▃▃▁▃▂▃▃▃▃▃▃▂▁▃▃▁▂▂▂▂▁▂▂
wandb:   trainer/global_step ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▆▇▇▇▇▇███
wandb: trainer/learning_rate ███▇▇▇▇▇▇▆▆▆▆▆▅▅▅▅▅▅▄▄▄▄▄▄▃▃▃▃▃▂▂▂▂▂▂▁▁▁
wandb:       validation/loss ▁
wandb: 
wandb: Run summary:
wandb:              batchidx 51
wandb:                 epoch 0
wandb:           global_rank 0
wandb:          real_ctx_len 4095
wandb:               substep 408
wandb:            train/loss 3.95312
wandb:   trainer/global_step 2546
wandb: trainer/learning_rate 0.0004
wandb:       validation/loss 3.60836
wandb: 
wandb: 🚀 View run v5-hs32-L6-D2048-E0.1 

In [7]:
# Lets export the model from the checkpoint
!cd "{TRAINER_DIR}" && \
    python export_checkpoint.py "../checkpoint/{FILENAME_PREFIX}-enwiki-4k/last.ckpt" "../model/{FILENAME_PREFIX}-enwiki-4k.pth" "bf16"
!cd "{TRAINER_DIR}" && ls -alh "../model/{FILENAME_PREFIX}-enwiki-4k.pth"

Setting ds_accelerator to cuda (auto detect)


Processing zero checkpoint '../checkpoint/v5-hs32-L6-D2048-E0_1-enwiki-4k/last.ckpt/checkpoint'


Detected checkpoint of type zero stage ZeroStageEnum.optimizer_states, world_size: 8


Parsing checkpoint created by deepspeed==0.9.3


Reconstructed fp32 state dict with 126 params 533234432 elements
Saving bf16 state dict to ../model/v5-hs32-L6-D2048-E0_1-enwiki-4k.pth


-rw-r--r-- 1 root root 1018M Aug 26 10:17 ../model/v5-hs32-L6-D2048-E0_1-enwiki-4k.pth


In [8]:
# # Lets do a quick dragon prompt validation
!cd "{INFERENCE_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python3 dragon_test.py "../model/{FILENAME_PREFIX}-enwiki-4k.pth" "cuda fp32"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


--- DRAGON PROMPT ---
In a shocking finding, scientist discovered a herd of dragons living in a remote, previously unexplored valley, in Tibet. Even more surprising to the researchers was the fact that the dragons spoke perfect Chinese.

 It

 was

...

 that

 there

 was

 a

 variety


In [9]:
# Lets do a quick memory test
!export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
        python3 ../memory_script/eval_v5_memory_guided.py "{PROJECT_DIR}/model/{FILENAME_PREFIX}-enwiki-4k.pth"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


Traceback (most recent call last):
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32/../memory_script/eval_v5_memory_guided.py", line 366, in <module>
    asyncio.run(main_function())
  File "/usr/lib/python3.11/asyncio/runners.py", line 190, in run
    return runner.run(main)
           ^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/asyncio/runners.py", line 118, in run
    return self._loop.run_until_complete(task)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/usr/lib/python3.11/asyncio/base_events.py", line 653, in run_until_complete
    return future.result()
           ^^^^^^^^^^^^^^^
  File "/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32/../memory_script/eval_v5_memory_guided.py", line 58, in main_function
    model = SimpleRWKV(model_path, device="cuda")
            ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/actions-runner/_work/RWKV-infctx-tra

# Enwiki Stage 2 : Basic Instruct Tuning

In [10]:
# Lets preload the requried dataset
!cd "{TRAINER_DIR}" && \
    python3 preload_datapath.py "{NOTEBOOK_DIR}/v5base-enwiki-instruct.yaml"

Found cached dataset parquet (/actions-runner/.cache/huggingface/datasets/c-s-ale___parquet/c-s-ale--dolly-15k-instruction-alpaca-format-9dfbb23260d63d9d/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7)
100%|████████████████████████████████████████████| 1/1 [00:00<00:00, 677.92it/s]


Loading cached processed dataset at /actions-runner/.cache/huggingface/datasets/c-s-ale___parquet/c-s-ale--dolly-15k-instruction-alpaca-format-9dfbb23260d63d9d/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-3a81f68e4498c60a_*_of_00064.arrow


Loading cached processed dataset at /actions-runner/.cache/huggingface/datasets/c-s-ale___parquet/c-s-ale--dolly-15k-instruction-alpaca-format-9dfbb23260d63d9d/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-36c9ee56cc63a264_*_of_00064.arrow
Loading cached split indices for dataset at /actions-runner/.cache/huggingface/datasets/c-s-ale___parquet/c-s-ale--dolly-15k-instruction-alpaca-format-9dfbb23260d63d9d/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-4f2b89ca1acce20d.arrow and /actions-runner/.cache/huggingface/datasets/c-s-ale___parquet/c-s-ale--dolly-15k-instruction-alpaca-format-9dfbb23260d63d9d/0.0.0/14a00e99c0d15a23649d0db8944380ac81082d4b021f398733dd84f3a6c569a7/cache-c7f7bd164be56255.arrow


Saving the dataset (0/1 shards):   0%|         | 0/14932 [00:00<?, ? examples/s]

In [11]:
# Start the instruct finetuning
!cd "{TRAINER_DIR}" && \
    export WANDB_MODE="{WANDB_MODE}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python lightning_trainer.py fit \
        -c "{NOTEBOOK_DIR}/v5base-enwiki-instruct.yaml" \
        --trainer.logger.init_args.name="{WANDB_PREFIX} - Enwiki-Instruct (train-ctx=4k, {DEEPSPEED_STRAT})" \
        --trainer.strategy="{DEEPSPEED_STRAT}" \
        --trainer.devices="{GPU_DEVICES}" \
        --trainer.callbacks.init_args.dirpath="../checkpoint/{FILENAME_PREFIX}-enwiki-instruct/" \
        --model.load_model="../model/{FILENAME_PREFIX}-enwiki-4k.pth" \
        --model.ctx_len=4096 \
        --model.bptt_learning_range=1

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


/usr/local/lib/python3.11/dist-packages/lightning/pytorch/cli.py:484: UserWarning: LightningCLI's args parameter is intended to run from within Python like if it were from the command line. To prevent mistakes it is not recommended to provide both args and command line arguments, got: sys.argv[1:]=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32/v5base-enwiki-instruct.yaml', '--trainer.logger.init_args.name=v5-hs32-L6-D2048-E0.1 - Enwiki-Instruct (train-ctx=4k, deepspeed_stage_1)', '--trainer.strategy=deepspeed_stage_1', '--trainer.devices=auto', '--trainer.callbacks.init_args.dirpath=../checkpoint/v5-hs32-L6-D2048-E0_1-enwiki-instruct/', '--model.load_model=../model/v5-hs32-L6-D2048-E0_1-enwiki-4k.pth', '--model.ctx_len=4096', '--model.bptt_learning_range=1'], args=['fit', '-c', '/actions-runner/_work/RWKV-infctx-trainer/RWKV-infctx-trainer/notebook/experiment/rwkv-x-exp/v5-headsize32/v5base-enwiki-instruct.yaml'

/usr/local/lib/python3.11/dist-packages/lightning/fabric/utilities/seed.py:39: UserWarning: No seed found, seed set to 68094276
  rank_zero_warn(f"No seed found, seed set to {seed}")
Global seed set to 68094276


wandb: Currently logged in as: picocreator (rwkv-x-dev). Use `wandb login --relogin` to force relogin


...


Validation DataLoader 0: 100%|██████████████████| 10/10 [00:02<00:00,  3.62it/s]

Epoch 0: 100%|█| 1867/1867 [16:54<00:00,  1.84it/s, v_num=s2ag, train/loss=2.310
Epoch 0: 100%|█| 1867/1867 [16:54<00:00,  1.84it/s, v_num=s2ag, train/loss=2.310

`Trainer.fit` stopped: `max_epochs=1` reached.
Epoch 0: 100%|█| 1867/1867 [16:58<00:00,  1.83it/s, v_num=s2ag, train/loss=2.310


wandb: Waiting for W&B process to finish... (success).


wandb: 
wandb: Run history:
wandb:              batchidx ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███▁
wandb:                 epoch ▁▁▁▁▁▁▁▁▁▁
wandb:           global_rank ▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁
wandb:          real_ctx_len ▄▁▁▂▂▂▁▁▂▁▁▂▁▁▁▁▁▁▃▂▁▁▂▁▃▁▁▃▁▁▁█▁▂▁▁▁▁▂▁
wandb:               substep ▁▁▁▂▂▂▂▂▂▃▃▃▃▃▄▄▄▄▄▄▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███▁
wandb:            train/loss ▄▃▄▅█▅▅▃█▄▄▄▅▆▆▆▇▃▅▅▃▅▅▅▆▃▇▅▁▇▄▃▅▇▇█▅▇▆▅
wandb:   trainer/global_step ▁▁▁▁▂▂▂▂▂▃▃▃▃▃▃▄▄▄▄▄▅▅▅▅▅▅▆▆▆▆▆▇▇▇▇▇▇███
wandb: trainer/learning_rate ████▇▇▇▇▇▆▆▆▆▆▆▅▅▅▅▅▄▄▄▄▄▄▃▃▃▃▃▂▂▂▂▂▂▁▁▁
wandb:       validation/loss ▁
wandb: 
wandb: Run summary:
wandb:              batchidx 9
wandb:                 epoch 0
wandb:           global_rank 0
wandb:          real_ctx_len 85
wandb:               substep 72
wandb:            train/loss 3.95312
wandb:   trainer/global_step 466
wandb: trainer/learning_rate 0.0003
wandb:       validation/loss 3.1939
wandb: 
wandb: 🚀 View run v5-hs32-L6-D2048-E0.1 - Enwiki-Instruct (train-ctx=4k, dee

In [12]:
# Lets export the model from the checkpoint
!cd "{TRAINER_DIR}" && \
    python export_checkpoint.py "../checkpoint/{FILENAME_PREFIX}-enwiki-instruct/last.ckpt" "../model/{FILENAME_PREFIX}-enwiki-instruct.pth" "bf16"
!cd "{TRAINER_DIR}" && ls -alh "../model/{FILENAME_PREFIX}-enwiki-instruct.pth"

Setting ds_accelerator to cuda (auto detect)


Processing zero checkpoint '../checkpoint/v5-hs32-L6-D2048-E0_1-enwiki-instruct/last.ckpt/checkpoint'


Detected checkpoint of type zero stage ZeroStageEnum.optimizer_states, world_size: 8


Parsing checkpoint created by deepspeed==0.9.3


Reconstructed fp32 state dict with 126 params 533234432 elements
Saving bf16 state dict to ../model/v5-hs32-L6-D2048-E0_1-enwiki-instruct.pth


-rw-r--r-- 1 root root 1018M Aug 26 10:38 ../model/v5-hs32-L6-D2048-E0_1-enwiki-instruct.pth


In [13]:
# # Lets do a quick dragon prompt validation
!cd "{INFERENCE_DIR}" && \
    export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
    python3 dragon_test.py "../model/{FILENAME_PREFIX}-enwiki-instruct.pth" "cuda fp32"

Setting ds_accelerator to cuda (auto detect)


[RWKV.model] Running RWKV model using 'torch-jit' with torch '2.0.1+cu118'


--- DRAGON PROMPT ---
In a shocking finding, scientist discovered a herd of dragons living in a remote, previously unexplored valley, in Tibet. Even more surprising to the researchers was the fact that the dragons spoke perfect Chinese.

 Then

,

...

 was

 in

 fact

 a

 tiger


In [14]:
# # Lets do a quick memory test
# !export RWKV_WAVENET_LAYERS="{RWKV_WAVENET_LAYERS}" && \
#         python3 ../memory_script/eval_v5_memory_guided.py "{PROJECT_DIR}/model/{FILENAME_PREFIX}-enwiki-instruct.pth"